## Zero-Shot Classification for Bias

In this notebook, we will use zero-shot classification with pretrained transformers to score bias of the commentators.

Zero-shot classification is a great strategy for unlabeled data.  I can use a pretrained language model such as BERT, RoBERTa, or BART to classify the games' into categories.  

There are a few well-suited pretrained transformers for my task:
- `sentence-transformers/paraphrase-mpnet-base-v2` is excellent for semantic similiarity, clustering, and ranking.
- `facebook/bart-large-mnli` is an encoder-decoder (seq2seq) model backed by Hugging Face's zero-shot pipeline.  It yields excellent results for Natural Langauge Inference (NLI) tasks using the premise-hypothesis framework. It's the most commonly used model for this type of task.
- `roberta-large-mnli` is similiar to BART but based on the RoBERTa framework.  It is slightly more complex than BART possibly giving me more accurate results than BART.  This model works well for precision-focused types of tasks.

We will use raw game transcript instead of our tokenized data.  Zero-shot classification pipeline will tokenize our text and compute embeddings on its own.  Without it, the embeddings and classification heads could mismatch leading to spurious inference results.

In [1]:
from transformers import pipeline
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

# Load our data
data = pd.read_json("../dataset/preprocessed_data.json")



/Users/tommayer/.pyenv/versions/3.12.6/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
!pip install tf-keras
!pip install --upgrade transformers
!pip install torch

  Using cached numpy-2.1.3-cp312-cp312-macosx_14_0_arm64.whl.metadata (62 kB)
Using cached numpy-2.1.3-cp312-cp312-macosx_14_0_arm64.whl (5.1 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 2.2.4
    Uninstalling numpy-2.2.4:
      Successfully uninstalled numpy-2.2.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gensim 4.3.3 requires numpy<2.0,>=1.18.5, but you have numpy 2.1.3 which is incompatible.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.4/10.4 MB 40.2 MB/s eta 0:00:00 0:00:01
  Attempting uninstall: transformers
    Found existing installation: transformers 4.51.0
    Uninstalling transformers-4.51.0:
      Successfully uninstalled transformers-4.51.0


I will analyze bias using zero-shot classification on the data.  I'll start with Meta's BART model.

In [3]:
data.head()

game_id  \
0          1962-houston_oilers-dallas_texans.txt   
1       1969-chicago_bears-green_bay_packers.txt   
2  1969-cleveland_browns-minnesota_vikings-1.txt   
3    1969-cleveland_browns-minnesota_vikings.txt   
4         1969-new_york_jets-baltimore_colts.txt   

                                   teams  \
0        [houston_oilers, dallas_texans]   
1     [chicago_bears, green_bay_packers]   
2  [cleveland_browns, minnesota_vikings]   
3  [cleveland_browns, minnesota_vikings]   
4       [new_york_jets, baltimore_colts]   

                                          transcript  year  \
0  gilson well defend the goal on your left theyl...  1962   
1  cbs television sports presents the national fo...  1969   
2  the nfl today brought to you by the foundation...  1969   
3  the nfl today brought to you by the foundation...  1969   
4  &gt;&gt; nbc sports presents the third nflafl ...  1969   

                                              tokens  \
0  [gilson, well, defend, the, goal, on, your, le...   
1  [cbs, television, sports, presents, the, natio...   
2  [the, nfl, today, brought, to, you, by, the, f...   
3  [the, nfl, today, brought, to, you, by, the, f...   
4  [gtgt, nbc, sports, presents, the, third, nfla...   

                                       doc_embedding broadcaster  
0  [0.0272845495, 0.0167274754, 0.0260243993, 0.0...         ABC  
1  [0.0302205924, 0.014963325100000001, 0.0228471...         CBS  
2  [0.027876755200000002, 0.0162593126, 0.0226585...         CBS  
3  [0.028167814000000003, 0.016339412, 0.02250985...         CBS  
4  [0.0310913976, 0.0153203607, 0.024078829200000...         NBC

In [4]:
def zero_shot(row):
    """ Baseline model using zero-shot classification with BART """
    # load model
    model = pipeline("zero-shot-classification", model="facebook/bart-large-mnli")

    # label the teams home and away
    away_team, home_team = row['teams'] # splits on the teams column, away team is first

    # these NEED good context - phrasing is key for getting successful results
    labels = [f"commentary favors {away_team}",
               f"commentary favors {home_team}", 
               f"neutral commentary"]
    
    # get the sequence
    transcript = row['transcript']

    chunk_size = 256
    # broken up the transcript into chunks of 256 tokens within each game
    # each row is kept in the same row (chunks don't cross game boundaries)
    chunks = [transcript[i:i+chunk_size] for i in range(0, len(transcript), chunk_size)]

    # results
    results = []
    for chunk in chunks:
        try:
            result = model(chunk, labels, 
                           hypothesis_template=f"The commentary is about {away_team} and {home_team}.")
            results.append(result)
        except Exception as e:
            print(f'Error in processing chunk: {e}')
            continue # so we don't break the loop

    # compile the results
    away_score = []
    home_score = []
    neutral_score = []

    # loop through the results and compile our scores now
    for result in results: 
        labels = result['labels']
        scores = result['scores']
        for label, score in zip(labels, scores):
            if f"favors {away_team}" in label:
                away_score.append(score)
            elif f"favors {home_team}" in label:
                home_score.append(score)
            else:
                neutral_score.append(score)

    # Now return after processing all results
    return {
        'game_id': row['game_id'],
        'year': row['year'],
        'team1': away_score,
        'team2': home_score,
        'team1_bias': np.mean(away_score) if away_score else 0,
        'team2_bias': np.mean(home_score) if home_score else 0,
        'neutrality': np.mean(neutral_score) if neutral_score else 0,
        'bias_score': abs(np.mean(away_score) - np.mean(home_score)) if away_score and home_score else 0
    }

    
    

Process the games, show the results.

In [5]:
def get_bias(data):
    """ Takes the previous function and applies it to my data """
    results = []

    for idx, row in data.iterrows():
        try:
            bias_metrics = zero_shot(row)
            results.append(bias_metrics)
        except Exception as e:
            print(f"We are getting an error here: {e}")
    
    return pd.DataFrame(results)

In [6]:
sample_size = int(len(data) * 0.05)  # 5% of data
data_sample = data.sample(n=sample_size, random_state=42)  # random_state for reproducibility

Get some visuals for my data to show in my final paper.

In [18]:
def plot_bias(results_df):
    """ Show the bias plots """
    fig, axes = plot.subplots(1, 2, figsize=(15, 5))
    # 1. Bias distribution over years
    sns.boxplot(data=results_df, x='year', y='bias_score', 
                ax=axes[0,0])
    axes[0,0].set_title('Commentary Bias Over Years')
    axes[0,0].set_xticklabels(axes[0,0].get_xticklabels(), rotation=45)
    
    # 2. Team bias comparison
    bias_long = pd.melt(results_df, 
                       value_vars=['team1_bias', 'team2_bias'],
                       var_name='team', value_name='bias')
    sns.boxplot(data=bias_long, x='team', y='bias',
                ax=axes[0,1])
    axes[0,1].set_title('Team Bias Comparison')
    
    # 3. Neutrality over time
    sns.lineplot(data=results_df, x='year', y='neutrality',
                ax=axes[1,0])
    axes[1,0].set_title('Commentary Neutrality Over Time')
    
    # 4. Bias vs Neutrality
    sns.scatterplot(data=results_df, x='bias_score', y='neutrality',
                    ax=axes[1,1])
    axes[1,1].set_title('Bias vs Neutrality')
    
    plt.tight_layout()
    plt.show()


In [7]:
# Run the analysis
print("Starting bias analysis...")
bias_results = get_bias(data_sample)

# Plot results
plot_bias(bias_results)

# Print summary statistics
print("\nBias Analysis Summary:")
print(bias_results[['bias_score', 'neutrality']].describe())

# Find most biased games
print("\nTop 5 Most Biased Games:")
print(bias_results.nlargest(5, 'bias_score')[
    ['game_id', 'team1', 'team2', 'bias_score', 'neutrality']
])

# Analyze bias trends over time
yearly_bias = bias_results.groupby('year').agg({
    'bias_score': ['mean', 'std'],
    'neutrality': 'mean'
}).round(3)

print("\nYearly Bias Trends:")
print(yearly_bias)

Starting bias analysis...


Device set to use mps:0


Error in processing chunk: The provided hypothesis_template "The commentary is about auburn and florida." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about auburn and florida." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about auburn and florida." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about auburn and florida." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the l

Device set to use mps:0


Error in processing chunk: The provided hypothesis_template "The commentary is about navy and south_florida." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about navy and south_florida." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about navy and south_florida." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about navy and south_florida." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such a

...

Error in processing chunk: The provided hypothesis_template "The commentary is about pittsburgh_steelers and miami_dolphins." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about pittsburgh_steelers and miami_dolphins." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about pittsburgh_steelers and miami_dolphins." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about pittsburgh_steelers and miami_dolphins." was not able to be formatted with the target labels.

Device set to use mps:0


Error in processing chunk: The provided hypothesis_template "The commentary is about new_mexico and ohio." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about new_mexico and ohio." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about new_mexico and ohio." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where the label should go.
Error in processing chunk: The provided hypothesis_template "The commentary is about new_mexico and ohio." was not able to be formatted with the target labels. Make sure the passed template includes formatting syntax such as {} where t

Device set to use mps:0


KeyboardInterrupt: 